In [1]:
import numpy as np

# Try Supervised/Unsupervised Learning using only word counts:

In contrast to the topic modeling approach: see if the raw text yields better results?

## Read in character JSON, build feature vectors for a BOW-type model

Things to do: Fiddle with the mention threshold, dialogue features (to include or not to include?), maybe throw out the most common attributes afterward

**NOTE: All of this functionality is now located in the loadCharFeatures module**

In [2]:
import loadCharFeatures
reload(loadCharFeatures)
(characters, character_namelists, total_features, top_n) = loadCharFeatures.getCharVectorsFromJson(use_stopwords = False, 
                                                                                                   mention_threshold = 50)

Most common words in book:  [('the', 47552.0), ('to', 26268.0), ('and', 25179.0), ('of', 21444.0), ('a', 19852.0), ('.', 17618.0), ('was', 15155.0), ('he', 14435.0), ('his', 13612.0), ('said', 12682.0), ('in', 11952.0), ('Harry', 11326.0), ('had', 9954.0), ('that', 8840.0), ('at', 8322.0), ('you', 8044.0), ('it', 7310.0), ('I', 7282.0), ('as', 7026.0), ('with', 6272.0), ('on', 6097.0), ('for', 5193.0), ('He', 4990.0), ('not', 4666.0), ('\xc2\x91', 4527.0), ('her', 4418.0), ('they', 4259.0), ('be', 4258.0), ('were', 4155.0), ('but', 4010.0), ('from', 3997.0), ('have', 3970.0), ('out', 3847.0), ('him', 3806.0), ('\xe2\x80\x94', 3561.0), ('she', 3462.0), ('up', 3432.0), ('into', 3427.0), ('Ron', 3366.0), ('all', 3336.0), ('The', 3250.0), ('been', 3136.0), ('Hermione', 3119.0), ('what', 2798.0), ('could', 2668.0), ('back', 2595.0), ('who', 2581.0), ('their', 2497.0), ('is', 2491.0), ('them', 2482.0), ('Harry,', 2400.0), ('\xe2\x80\x9cI', 2326.0), ('looked', 2321.0), ('about', 2282.0), ('so

In [3]:
texts = [None for key in characters]
names = {}
i = 0
for key, value in characters.iteritems():
    print str(key) + ": " + str(value)
    texts[i] = value
    names[i] = key
    i += 1
    print
print len(characters)
print texts

Fang: [u'take_PATIENT', u'use_PATIENT', u'swept_PATIENT', u'bless_PATIENT', u'take_PATIENT', u'fend_PATIENT', u'leav_PATIENT', u'carri_PATIENT', u'push_PATIENT', u'bowl_PATIENT', u'stroke_PATIENT', u'found_PATIENT', u'want_PATIENT', u'transfix_PATIENT', u'said_AGENT', u'start_AGENT', u'said_AGENT', u'went_AGENT', u'bound_AGENT', u'let_AGENT', u'yelp_AGENT', u'seem_AGENT', u'kept_AGENT', u'whimper_AGENT', u'fight_AGENT', u'thud_AGENT', u'howl_AGENT', u'howl_AGENT', u'fling_himself_AGENT', u'trembl_AGENT', u'ter_AGENT', u'shove_i_AGENT', u'lollop_AGENT', u'gallop_AGENT', u'save__AGENT', u'move_AGENT', u'reach_edg_AGENT', u'stop_AGENT', u'feel_chil_AGENT', u'had_AGENT', u'control_own_AGENT', u'breath_AGENT', u'cling_AGENT', u'thought_AGENT', u'pull_it_AGENT', u'stare_AGENT', u'want_tim_AGENT', u'press_met_AGENT', u'lower_hand_AGENT', u'whimper_AGENT', u'won_AGENT', u'scratch_whin_AGENT', u'bark_AGENT', u'launch_himself_AGENT', u'trot_AGENT', u'bound_AGENT', u'strode_AGENT', u'give_bark_AG

In [4]:
from gensim import corpora, models, similarities

dictionary = corpora.Dictionary(texts)
print len(dictionary)

corpus = [dictionary.doc2bow(text) for text in texts]
# for (name, chardoc) in zip(names, corpus):
#     print name
#     for word_tup in chardoc:
#         print word_tup[0], word_tup[1]

18777


## TF-IDF + Cosine Similarity

In [5]:
tfidf = models.TfidfModel(corpus)

corp_tfidf = tfidf[corpus]

sim_index = similarities.MatrixSimilarity(corp_tfidf, num_features = len(dictionary))
with open('tfidf_sims.txt', 'w+') as f:
    for doc in list(enumerate(sim_index)):
        top_indices = np.argsort(doc[1])
        print "Most similar to", names[doc[0]], ":"
        f.write("Most similar to "+str(names[doc[0]])+":\n")
        j = 0
        top_indices = top_indices[::-1]
        for i in top_indices:
            if j != 0:
                print j, ".",names[i], doc[1][i]
                f.write(str(j)+". "+str(names[i])+" "+str(doc[1][i])+'\n')
            j+=1
            if j == 11:
                break
        print
        f.write('\n')
f.close()

Most similar to Fang :
1 . Harry 0.116808
2 . Hagrid 0.115615
3 . Ron 0.100433
4 . Malfoy 0.0851769
5 . Hermione 0.0851557
6 . Dumbledore 0.0752489
7 . Crookshanks 0.0663826
8 . Snape 0.0654016
9 . George 0.0625973
10 . Neville 0.0622018

Most similar to Lupin :
1 . Hermione 0.483064
2 . Dumbledore 0.457149
3 . Ron 0.455022
4 . Harry 0.432117
5 . Snape 0.374171
6 . Sirius 0.349558
7 . Molly Weasley 0.317348
8 . Fred 0.310145
9 . Mr. Weasley 0.305693
10 . Ginny 0.291045

Most similar to Dudley :
1 . Harry 0.234318
2 . Ron 0.192153
3 . Malfoy 0.16627
4 . Hermione 0.162986
5 . Sirius 0.148596
6 . Ginny 0.140068
7 . Snape 0.137869
8 . Dumbledore 0.136239
9 . Voldemort 0.126867
10 . Neville 0.124998

Most similar to Cho :
1 . Harry 0.258439
2 . Ron 0.236688
3 . Hermione 0.222488
4 . Dumbledore 0.169879
5 . Ginny 0.159553
6 . Fred 0.14708
7 . Sirius 0.143788
8 . Snape 0.135373
9 . Malfoy 0.133999
10 . Molly Weasley 0.129449

Most similar to Fred :
1 . Ron 0.541655
2 . Hermione 0.516747
3 . G

## Logistic Regression (this time with raw BOW model)

In [6]:
# load our labeled character data (choose one of our annotated character files)
import getVectors
getVectors = reload(getVectors)
labels = ['Muggles', 'Hogwarts Students', 'Hogwarts Teachers', 'Ministry Officials', 
          'Quidditch Players', 'Gryffindors', 'Ravenclaws', 'Hufflepuffs','Slytherins',
         'Muggle-borns','Purebloods','Half-bloods','Humans','Part Humans', 'Non-Humans',
         'Death Eaters', 'Order of the Phoenix', 'Dumbledores Army','Animagi', 'Parselmouths',
         'Convicts','Weasleys','Dead','Bullies', 'Victims']
(vectors, charlist) = getVectors.getVectors("cluster.txt")
# labels = ['Protagonists', 'Antagonists', 'Neutral', 'Animals']
# (vectors, charlist) = getVectors.getVectors("good_bad_labels.txt")
print charlist

['Dudley', 'Mr. Dursley', 'Mrs. Dursley', 'Aunt Marge', 'Frank Bryce', 'Mrs. Figg', 'Mr. Roberts', 'Mrs. Cole', 'Harry Potter', 'Ron Weasley', 'Hermione Granger', 'Fred Weasley', 'George Weasley', 'Hannah Abbott', 'Draco Malfoy', 'Neville Longbottom', 'Ginny Weasley', 'Percy Weasley', 'Luna Lovegood', 'Cedric Diggory', 'Vincent Crabbe', 'Dean Thomas', 'Seamus Finnigan', 'Oliver Wood', 'Cho Chang', 'Gregory Goyle', 'Katie Bell', 'Parvati Patil', 'Lee Jordan', 'Ernie Macmillan', 'Colin Creevey', 'Cormac McLaggen', 'Alicia Spinnet', 'Pansy Parkinson', 'Zacharias Smith', 'Justin Finch-Fletchley', 'Lavender Brown', 'Zabini ', 'Marietta', 'Roger Davies', 'Angelina Johnson', 'Montague', 'Michael Corner', 'Warrington', 'Leanne', 'Padma Patil', 'Romilda Vane', 'Dennis Creevey', 'Albus Dumbledore', 'Rubeus Hagrid', 'Severus Snape', 'Minerva McGonagall', 'Dolores Umbridge', 'Remus Lupin', 'Mad-Eye Moody', 'Horace Slughorn', 'Gilderoy Lockhart', 'Trelawney', 'Flitwick', 'Quirrell', 'Madam Pomfrey'

In [7]:
# get a list of the indices for labeled characters that were recognized by book-nlp 
# (if they weren't returned in the character list, we can't classify them)
labeled = {}
j = 0 # index of character in labeled character list
for name in charlist:
    i = 0 # index of character in topic model vectors list
    found = False
    for name2 in names:
        #print name2
        if name.encode('UTF-8') in character_namelists[names[name2]]:
            found = True
        elif not found == True:
            i+=1
    if found:
        # print name.encode('UTF-8')
        # tupe is topic vector index, charlist index
        labeled[name] = (j, i)
    #else:
        #print name.encode('UTF-8')
    j+=1
num_samples = len(labeled)
print num_samples

82


In [8]:
labeled_chars = []
corpus_labeled = []
matrix = []
for char in labeled:
    #print char
    (charNameIndex, charTopicIndex) = labeled[char]
    #print charNameIndex, charTopicIndex
    #print charlist[charNameIndex]
    labeled_chars.append(charlist[charNameIndex])
    #print vectors[charNameIndex]
    matrix.append(vectors[charNameIndex])
    #print corpus[charTopicIndex]              
    corpus_labeled.append(corpus[charTopicIndex])
    #print

from gensim import matutils
terms = len(dictionary.values())
labeled_bow_matrix = matutils.corpus2dense(corpus_labeled, num_docs=len(corpus_labeled), num_terms=terms)
print labeled_bow_matrix.T.shape

labelmatrix = np.matrix(matrix)
print labelmatrix.shape

(82L, 18777L)
(82L, 25L)


In [12]:
from sklearn import linear_model
from sklearn import cross_validation

accuracies = []
precisions = []
recalls = []


# choose the appropriate row to get your binary labels for feature i, then split it into a train/test set
# i.e. Muggles vs. not muggles, good guys vs. not good guys, etc.
for label in range(labelmatrix[0].size):
    print labels[label]
    #X_train, X_test, y_train, y_test = cross_validation.train_test_split(labeled_topic_matrix, labelmatrix[:,label], test_size=0.4, random_state=0)
    logreg = linear_model.LogisticRegression(C=1e5)
    # train
    #logreg.fit(X_train, y_train)
    #Z = logreg.predict(X_test)
    #print "accuracy: ", logreg.score(X_test, y_test)
    # print Z
    print "Accuracy:"
    accuracyScores = cross_validation.cross_val_score(logreg, labeled_bow_matrix.T,  np.ravel(labelmatrix[:,label].T), cv=2)
    print np.average(accuracyScores)
    accuracies.extend(accuracyScores)
    print "Precision:"
    precisionScores = cross_validation.cross_val_score(logreg, labeled_bow_matrix.T,  np.ravel(labelmatrix[:,label].T), cv=2, scoring = 'precision')
    print np.average(precisionScores)
    precisions.extend(precisionScores)
    print "Recall:"
    recallScores = cross_validation.cross_val_score(logreg, labeled_bow_matrix.T,  np.ravel(labelmatrix[:,label].T), cv=2, scoring = 'recall')
    print np.average(recallScores)
    recalls.extend(recallScores)
    print

print "avg accuracy", np.average(accuracies)
print "avg precision", np.average(precisions)
print "avg recalls", np.average(recalls)

Muggles
Accuracy:
0.96369047619
Precision:
0.0
Recall:
0.0

Hogwarts Students
Accuracy:
0.756097560976
Precision:
0.65625
Recall:
0.5

Hogwarts Teachers
Accuracy:
0.891071428571
Precision:
0.9
Recall:
0.404761904762

Ministry Officials
Accuracy:
0.902976190476
Precision:
0.5
Recall:
0.125

Quidditch Players
Accuracy:
0.756097560976
Precision:
0.1
Recall:
0.0625

Gryffindors
Accuracy:
0.69512195122
Precision:
0.539772727273
Recall:
0.535714285714

Ravenclaws
Accuracy:
0.96369047619
Precision:
0.0
Recall:
0.0

Hufflepuffs
Accuracy:
0.963414634146
Precision:
0.0
Recall:
0.0

Slytherins
Accuracy:
0.90243902439
Precision:
0.833333333333
Recall:
0.3

Muggle-borns
Accuracy:
0.96369047619
Precision:
0.0
Recall:
0.0

Purebloods
Accuracy:
0.670731707317
Precision:
0.25
Recall:
0.208333333333

Half-bloods
Accuracy:
0.841666666667
Precision:
0.0
Recall:
0.0

Humans
Accuracy:
0.841463414634
Precision:
0.846581875994
Recall:
0.967741935484

Part Humans
Accuracy:
0.914880952381
Precision:
0.0
Recall: